# Data download from GCP

In [1]:
import pandas as pd
!gsutil cp gs://chem_dsrc/P0_Toxcast/Data/assay_df/335_all_assay_df.csv ./

Copying gs://chem_dsrc/P0_Toxcast/Data/assay_df/335_all_assay_df.csv...
- [1 files][  4.2 MiB/  4.2 MiB]                                                
Operation completed over 1 objects/4.2 MiB.                                      


In [1]:
# !conda install -c conda-forge imbalanced-learn

In [1]:
# rdkit 2020.03.3 버전 다운로드
# !pip install kora -q
# import kora.install.rdkit
import rdkit
import numpy
import pandas
import numpy as np
import pandas as pd

from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit import DataStructs
from rdkit.Chem import Draw
from rdkit.Chem.Draw import SimilarityMaps
from rdkit import Chem, DataStructs
from rdkit.Chem import MACCSkeys

from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.model_selection import StratifiedKFold

from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import roc_auc_score
from sklearn.metrics import recall_score
from sklearn.metrics import average_precision_score, precision_recall_curve
from sklearn.metrics import auc, plot_precision_recall_curve
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import matthews_corrcoef

from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB

from imblearn.combine import SMOTEENN 
from sklearn import metrics

In [2]:
# !conda install -c rdkit rdkit

In [8]:
import os 
import time

ffpp_list = ['maccs', 'morgan','rdkit','pattern','layerd']
algo_list = ['MLP','GBT','RF','LR','KNN','NB']

In [9]:
import os 
import time

ffpp_list = ['maccs', 'morgan','rdkit','pattern','layerd']
algo_list = ['MLP','GBT','RF','LR','KNN','NB']

dir_path = './result_sklearn_all_a_fp/'
os.mkdir(dir_path)
os.mkdir(dir_path + "metric/")

for i in ffpp_list : 
  os.mkdir(dir_path + "metric/"+i)

for i in ffpp_list : 
  for algo in algo_list :
    os.mkdir(dir_path + "metric/"+i+'/'+algo)



FileExistsError: [Errno 17] File exists: './result_sklearn_all_a_fp/'

In [10]:
def g_tf(ss_fp) : 
  # ss_fp = a_p_list[10]
  ffpp = ss_fp[0]#fingerfrint name
  ss =ss_fp[1]#assay name
  algo = ss_fp[2]

  start_time = time.time()
  print(ffpp ,algo, ss, 'start!_______________________________')

  df_ss = df.loc[:,['smiles',ss]]
  df_ss = df_ss.dropna()
  assays_ss = df_ss.columns

  #Smiles --> MACCS Keys
  assay = ss
  df_train  = df_ss[['smiles',ss] ]

  smiles_list = []
  err_smiles = []# fingerfrint로 변환시 에러 smiles
  fps = []
  enc_y = []
  for index, row in df_train.iterrows():

    if row[-1] == 'N' : 
      target = 0
    else :
      target = 1

    try : 
      mol = Chem.MolFromSmiles(row['smiles'])
      
      if ffpp == 'maccs' :    
          fp = MACCSkeys.GenMACCSKeys(mol)
      elif ffpp == 'morgan' : 
          fp = Chem.AllChem.GetMorganFingerprintAsBitVect(mol, 2)
      elif ffpp == 'rdkit' : 
          fp = Chem.RDKFingerprint(mol)
      elif ffpp == 'pattern' : 
          fp = Chem.rdmolops.PatternFingerprint(mol)
      elif ffpp == 'layerd' : 
          fp = Chem.rdmolops.LayeredFingerprint(mol)
      else : 
          print("fingerfrint selection error!")
          
      smiles_list.append(row['smiles'])   
      fps.append(fp)
      enc_y.append(target)
    except : 
      err_smiles.append(row['smiles'])
      pass

  np_fps = []
  for fp in fps:
    arr = numpy.zeros((1,))
    DataStructs.ConvertToNumpyArray(fp, arr)
    np_fps.append(arr)

  np_fps_array = numpy.array(np_fps)

#   print("변환 에러난 smiles 개수 : ", len(err_smiles), err_smiles)

  x_train_res, y_train_res = np_fps_array, np.array(enc_y)
  train = pd.DataFrame(data=x_train_res)
  train['label'] = y_train_res

  d = pd.DataFrame(columns = ['smiles','Type'] )
  d['smiles'] = smiles_list
  d['Type'] = enc_y

  #모든 물질에 대한 fingerprint를 string형태로 바꾼다(비교하기위함).
  mychems = []
  for item in np_fps:
      #print(item)
      item = np.array(item,dtype=int) #왜 굳이 두번? int형으로 추가하려면 이렇게 하면 되는구나....
      s = item.tolist() #넘파이어레이를 리스트로 바꾼다. 
      t = [str(i) for i in s]
      mychems.append(''.join(t))

  i = 0
  counter = 0
  chemdict = {} #딗셔너리.
  listofdups = []
  for item in mychems:
      try:
          chemdict[str(item)].append(i)
          #print('dup found')
          for j in range(len(chemdict[str(item)])):
              if (d['Type'][i] != d['Type'][chemdict[str(item)][j]]) :
                  listofdups.append(i)
                  counter+=1
      except: 
          #print('adding new')
          chemdict[str(item)] = []
          chemdict[str(item)].append(i)
      i+=1
  # print(str(counter)+' '+str(len(list(set(listofdups)))))
  #smote적용하기 전에서 listofdups를 빼면 된다!

  dups_list = list(set(listofdups))

  dups_list_0 = []
  for index in dups_list : 
    if train.iloc[index].label == 0 :
      dups_list_0.append(index)

  train = train.drop(dups_list_0)

  #분산이 0인 feature 제거
  train = train.loc[ :, train.std() > 0]



  # rskf = RepeatedStratifiedKFold(n_splits=10, n_repeats=10, random_state=36851234) 
  rskf = StratifiedKFold(n_splits = 10, shuffle = True, random_state = 42)
  sme = SMOTEENN(random_state=42, sampling_strategy = "minority")

  X = np.array( train.drop('label', axis =1) )
  y = np.array(train.label)

  count = 0 
  rep = 0

  metric_df = pd.DataFrame(columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy'])
  metric_fold_df = pd.DataFrame(columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy'])

  for train_index, test_index in rskf.split(X, y): 
    X_train, X_test = X[train_index], X[test_index]
    y_train, y_test = y[train_index], y[test_index]
    if ss in ['NVS_ADME_hCYP1A2' , 'NVS_ADME_hCYP2B6' , 'NCCT_TPO_AUR_dn'] : 
      pass
    else : 
      print("SMOTEENN fitiing....",ffpp,algo,ss)
      X_train, y_train = sme.fit_sample(X_train, list(y_train) )
      print("....End fitiing",ffpp, ss)

    if algo == 'MLP' : 
      clf = MLPClassifier()
    if algo == 'GBT' : 
      clf = GradientBoostingClassifier()
    if algo == 'RF' : 
      clf = RandomForestClassifier()
    if algo == 'LR' : 
      clf = LogisticRegression()
    if algo == 'KNN' : 
      clf = KNeighborsClassifier()
    if algo == 'NB' : 
      clf = GaussianNB()

    clf.fit(X_train, y_train)

    result =  clf.predict_proba(X_test) # 첫 클래스의 예측확률, 두번째 클래스의 예측 확률 어떤것이 0, 1이지?
    y_pred = clf.predict(X_test)
    conf_mat = confusion_matrix(y_test,y_pred)
    tn, fp, fn, tp = conf_mat.ravel()
    
    # Data to plot precision - recall curve
    precision_l, recall_l, thresholds = precision_recall_curve(y_test, result[:,1])
    # Use AUC function to calculate the area under the curve of precision recall curve

    auc_pr = auc(recall_l, precision_l)
    auc_roc =  roc_auc_score(y_test,result[:,1] )
    recall = tp/(tp+fn) # 실제 1인 것 중 모델이 1이라 한것의 비율
    specificity = tn / (fp+tn) # 실제 0인 것중 모델이 0이라한것의 비율
    b_a = (recall + specificity) / 2
    precision =  tp / (tp+fp)
    F1 = 2* (precision * recall) / (precision + recall)
    MCC = matthews_corrcoef(y_test,y_pred)
    accuracy = clf.score(X_test,y_test)


    metric_fold_df = metric_fold_df.append(pd.DataFrame([[auc_roc,auc_pr,b_a,recall,precision,F1,MCC,accuracy]],columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy']) )
    count +=1
    # print(ffpp, ss, count)
    if count % 10 == 0 :
      average = metric_fold_df.mean()
      std = metric_fold_df.std()
      metric_fold_df = metric_fold_df.append(average.to_frame().T)
      metric_fold_df = metric_fold_df.append(std.to_frame().T)
      metric_fold_df = round(metric_fold_df ,4)
      metric_fold_df.index = [str(rep) +'_' +  str(i) for i in range(10)]+ [str(rep)+'_Mean' , str(rep)+'_SD']
      metric_df = metric_df.append(metric_fold_df)
      metric_fold_df = pd.DataFrame(columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy'])
      rep += 1
      # print(ffpp, ss, rep)
    

  #전체 평균내기.
  bool_list = [] 
  for i in metric_df.index :
    if'Mean' in i  or 'SD' in i : 
      bool_list.append(False) 
    else : 
      bool_list.append(True)

  average = metric_df[bool_list].mean().to_frame().T
  average.index = ['Mean']
  std = metric_df[bool_list].std().to_frame().T
  std.index =['SD']

  metric_df = metric_df.append(round(average,4) )
  metric_df = metric_df.append(round(std,4))
  metric_df.to_csv(dir_path+"metric/"+ffpp+'/'+algo+'/'+ss+"_metric.csv")
  # end_time = time.time()
  print(ffpp ,algo, ss, 'end','time spent',start_time - time.time())
  

In [11]:
selected_assay_list = ['NVS_ADME_hCYP1A2' , 'NVS_ADME_hCYP2B6' , 'NCCT_TPO_AUR_dn','TOX21_AhR_LUC_Agonist', 'TOX21_Aromatase_Inhibition', 'TOX21_VDR_BLA_agonist_ratio', 'TOX21_VDR_BLA_antagonist_ratio', 'TOX21_AR_BLA_Agonist_ratio', 'TOX21_AR_BLA_Antagonist_ratio', 'TOX21_AR_LUC_MDAKB2_Agonist', 'TOX21_p53_BLA_p1_ratio', 'TOX21_p53_BLA_p2_ratio', 'TOX21_p53_BLA_p3_ratio', 'TOX21_p53_BLA_p4_ratio', 'TOX21_p53_BLA_p5_ratio', 'TOX21_HSE_BLA_agonist_ratio', 'TOX21_ELG1_LUC_Agonist', 'TOX21_ERa_BLA_Agonist_ratio', 'TOX21_ERa_BLA_Antagonist_ratio', 'TOX21_ESRE_BLA_ratio', 'TOX21_FXR_BLA_agonist_ratio', 'TOX21_FXR_BLA_antagonist_ratio', 'TOX21_GR_BLA_Agonist_ratio', 'TOX21_GR_BLA_Antagonist_ratio', 'TOX21_NFkB_BLA_agonist_ratio', 'TOX21_ARE_BLA_agonist_ratio', 'TOX21_TR_LUC_GH3_Agonist', 'TOX21_TR_LUC_GH3_Antagonist', 'TOX21_PPARg_BLA_Agonist_ratio', 'TOX21_PPARd_BLA_agonist_ratio', 'TOX21_PPARd_BLA_antagonist_ratio', 'TOX21_PPARg_BLA_antagonist_ratio']
selected_assay_list.remove('TOX21_NFkB_BLA_agonist_ratio')

ffpp_list = ['maccs', 'morgan','rdkit','pattern','layerd']

algo_list = ['MLP','GBT','RF','LR','KNN','NB']

a_p_list = []
for p in ffpp_list :
  for a in selected_assay_list : 
    for algo in algo_list :
      a_p_list.append([p,a,algo]) 

assay_name = '335_all_assay'
df = pd.read_csv('./Data/'+assay_name+"_df.csv")

In [12]:
import random
random.shuffle(a_p_list)
a_p_list

[['rdkit', 'TOX21_ELG1_LUC_Agonist', 'LR'],
 ['layerd', 'TOX21_TR_LUC_GH3_Agonist', 'MLP'],
 ['layerd', 'TOX21_p53_BLA_p3_ratio', 'LR'],
 ['layerd', 'TOX21_HSE_BLA_agonist_ratio', 'NB'],
 ['rdkit', 'NVS_ADME_hCYP2B6', 'GBT'],
 ['layerd', 'TOX21_PPARg_BLA_Agonist_ratio', 'RF'],
 ['morgan', 'TOX21_TR_LUC_GH3_Antagonist', 'MLP'],
 ['maccs', 'TOX21_p53_BLA_p1_ratio', 'LR'],
 ['morgan', 'TOX21_GR_BLA_Antagonist_ratio', 'GBT'],
 ['pattern', 'TOX21_ERa_BLA_Antagonist_ratio', 'LR'],
 ['rdkit', 'TOX21_ELG1_LUC_Agonist', 'GBT'],
 ['layerd', 'TOX21_TR_LUC_GH3_Agonist', 'NB'],
 ['layerd', 'TOX21_FXR_BLA_antagonist_ratio', 'NB'],
 ['maccs', 'TOX21_FXR_BLA_agonist_ratio', 'LR'],
 ['morgan', 'TOX21_GR_BLA_Agonist_ratio', 'LR'],
 ['morgan', 'TOX21_p53_BLA_p1_ratio', 'RF'],
 ['morgan', 'TOX21_AR_BLA_Agonist_ratio', 'MLP'],
 ['maccs', 'NCCT_TPO_AUR_dn', 'NB'],
 ['maccs', 'TOX21_p53_BLA_p5_ratio', 'GBT'],
 ['morgan', 'TOX21_PPARg_BLA_Agonist_ratio', 'LR'],
 ['pattern', 'TOX21_AhR_LUC_Agonist', 'MLP'],
 [

In [13]:
import warnings
warnings.filterwarnings(action='ignore')

In [16]:
import multiprocessing
CPU_CORE = multiprocessing.cpu_count() # 멀티프로세싱 CPU 사용 수
if __name__=='__main__':
    pool = multiprocessing.Pool(processes=CPU_CORE)
    pool.map(g_tf, a_p_list)
    pool.close()
    pool.join()  

layerdrdkitrdkitmorganpatternmaccs maccs   pattern layerdLRRFlayerd GBTpattern KNNMLPmaccspatternpattern maccs  pattern layerdMLPlayerd rdkitpattern rdkit   MLPrdkit  morgan patternKNNlayerd maccsTOX21_ELG1_LUC_AgonistTOX21_PPARg_BLA_Agonist_ratiopattern maccsRF   LRrdkitpatternTOX21_ELG1_LUC_Agonist KNNrdkitrdkit  layerdMLPpatternTOX21_GR_BLA_Antagonist_ratio pattern TOX21_AhR_LUC_AgonistmorganNBmorganlayerd NBrdkit  layerd NBpatternmaccs   patternmorganRF morganmaccs  TOX21_AR_BLA_Agonist_ratioMLPKNN    KNN   KNNMLP    TOX21_PPARd_BLA_agonist_ratioNB    morgan  GBTlayerd  KNNTOX21_p53_BLA_p1_ratio  MLP start!_______________________________ RFstart!_______________________________   LR NB TOX21_p53_BLA_p1_ratio   TOX21_AhR_LUC_AgonistRFGBTstart!_______________________________ TOX21_PPARd_BLA_agonist_ratioLRKNN  TOX21_VDR_BLA_antagonist_ratioLRstart!_______________________________MLP  NBstart!_______________________________NBTOX21_FXR_BLA_antagonist_ratio GBTNB  TOX21_ESRE_BLA_ratioLR  

RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not r

RDKit ERROR: [18:26:42] Explicit valence for atom # 4 C, 5, is greater than permitted
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [18:26:42] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [18:26:42] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [18:26:42] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [18:26:42] Explicit valence for atom # 0 F, 2, is greater than permitted
RDKit ERROR: [18:26:42] Explicit valence for atom # 4 C, 5, is greater than permitted
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [18:26:42] Explicit valence for atom # 0 O, 3, is greater than permitted


maccs NB NVS_ADME_hCYP2B6 

RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [18:26:42] Explicit valence for atom # 0 F, 2, is greater than permitted
RDKit WARNING: [18:26:42] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [18:26:42] Explicit valence for atom # 4 C, 5, is greater than permitted


...

SMOTEENN fitiing.... maccs LR TOX21_ELG1_LUC_Agonist
....End fitiing maccs TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... maccs LR TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit GBT TOX21_TR_LUC_GH3_Antagonist
....End fitiing layerd TOX21_ERa_BLA_Antagonist_ratio
....End fitiing pattern TOX21_FXR_BLA_agonist_ratio
....End fitiing maccs TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... maccs LR TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... layerd RF TOX21_ERa_BLA_Antagonist_ratio
....End fitiing maccs TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... maccs LR TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... pattern MLP TOX21_FXR_BLA_agonist_ratio
....End fitiing rdkit TOX21_TR_LUC_GH3_Antagonist
....End fitiing maccs TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... maccs LR TOX21_ELG1_LUC_Agonist
....End fitiing maccs TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... maccs LR TOX21_ELG1_LUC_Agonist
....End fitiing layerd TOX21_ERa_BLA_Antagonist_ratio
....End fitiing pattern TOX21_FXR_BLA_agonist_ratio
....End fitii

RDKit WARNING: [21:37:36] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [21:37:36] WARNING: not removing hydrogen atom without neighbors
[21:37:36] WARNING: not removing hydrogen atom without neighbors
[21:37:36] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [21:37:37] Explicit valence for atom # 0 F, 2, is greater than permitted
RDKit ERROR: [21:37:37] Explicit valence for atom # 4 C, 5, is greater than permitted
RDKit ERROR: [21:37:37] Explicit valence for atom # 0 O, 3, is greater than permitted
[21:37:37] Explicit valence for atom # 0 F, 2, is greater than permitted
[21:37:37] Explicit valence for atom # 4 C, 5, is greater than permitted
[21:37:37] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [21:37:37] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [21:37:37] Explicit valence for atom # 2 Cl, 2, is greater than permitted
RDKit ERROR: [21:37:37] Explicit valence for atom # 0 Cl, 2,

SMOTEENN fitiing.... layerd RF TOX21_ERa_BLA_Antagonist_ratio


RDKit ERROR: [21:37:39] Explicit valence for atom # 0 Cl, 2, is greater than permitted
[21:37:39] Explicit valence for atom # 0 Cl, 2, is greater than permitted
RDKit ERROR: [21:37:40] Explicit valence for atom # 0 N, 4, is greater than permitted
[21:37:40] Explicit valence for atom # 0 N, 4, is greater than permitted
RDKit ERROR: [21:37:42] SMILES Parse Error: syntax error while parsing: C[Sn](C)(|[O]C(=O)CCCCCC(C)(C)C)|[O]C(=O)CCCCCC(C)(C)C
RDKit ERROR: [21:37:42] SMILES Parse Error: Failed parsing SMILES 'C[Sn](C)(|[O]C(=O)CCCCCC(C)(C)C)|[O]C(=O)CCCCCC(C)(C)C' for input: 'C[Sn](C)(|[O]C(=O)CCCCCC(C)(C)C)|[O]C(=O)CCCCCC(C)(C)C'
[21:37:42] SMILES Parse Error: syntax error while parsing: C[Sn](C)(|[O]C(=O)CCCCCC(C)(C)C)|[O]C(=O)CCCCCC(C)(C)C
[21:37:42] SMILES Parse Error: Failed parsing SMILES 'C[Sn](C)(|[O]C(=O)CCCCCC(C)(C)C)|[O]C(=O)CCCCCC(C)(C)C' for input: 'C[Sn](C)(|[O]C(=O)CCCCCC(C)(C)C)|[O]C(=O)CCCCCC(C)(C)C'


SMOTEENN fitiing.... pattern MLP TOX21_FXR_BLA_agonist_ratio
SMOTEENN fitiing.... rdkit RF TOX21_PPARg_BLA_Agonist_ratio
....End fitiing layerd TOX21_ERa_BLA_Antagonist_ratio
....End fitiing pattern TOX21_FXR_BLA_agonist_ratio
SMOTEENN fitiing.... layerd RF TOX21_ERa_BLA_Antagonist_ratio
....End fitiing rdkit TOX21_PPARg_BLA_Agonist_ratio
SMOTEENN fitiing.... pattern MLP TOX21_FXR_BLA_agonist_ratio
SMOTEENN fitiing.... rdkit RF TOX21_PPARg_BLA_Agonist_ratio
....End fitiing layerd TOX21_ERa_BLA_Antagonist_ratio
....End fitiing pattern TOX21_FXR_BLA_agonist_ratio
SMOTEENN fitiing.... layerd RF TOX21_ERa_BLA_Antagonist_ratio
SMOTEENN fitiing.... pattern MLP TOX21_FXR_BLA_agonist_ratio
....End fitiing rdkit TOX21_PPARg_BLA_Agonist_ratio
SMOTEENN fitiing.... rdkit RF TOX21_PPARg_BLA_Agonist_ratio
....End fitiing layerd TOX21_ERa_BLA_Antagonist_ratio
....End fitiing pattern TOX21_FXR_BLA_agonist_ratio
SMOTEENN fitiing.... layerd RF TOX21_ERa_BLA_Antagonist_ratio
pattern MLP TOX21_FXR_BLA_ago

In [14]:
ss_fp = a_p_list[10]
ffpp = ss_fp[0]#fingerfrint name
ss =ss_fp[1]#assay name
# ffpp = "maccs"

df_ss = df.loc[:,['smiles',ss]]
df_ss = df_ss.dropna()
assays_ss = df_ss.columns

#Smiles --> MACCS Keys
assay = ss
df_train  = df_ss[['smiles',ss] ]

smiles_list = []
err_smiles = []# fingerfrint로 변환시 에러 smiles
fps = []
enc_y = []
for index, row in df_train.iterrows():

  if row[-1] == 'N' : 
    target = 0
  else :
    target = 1

  try : 
    mol = Chem.MolFromSmiles(row['smiles'])
    
    if ffpp == 'maccs' :    
        fp = MACCSkeys.GenMACCSKeys(mol)
    elif ffpp == 'morgan' : 
        fp = Chem.AllChem.GetMorganFingerprintAsBitVect(mol, 2)
    elif ffpp == 'rdkit' : 
        fp = Chem.RDKFingerprint(mol)
    elif ffpp == 'pattern' : 
        fp = Chem.rdmolops.PatternFingerprint(mol)
    elif ffpp == 'layerd' : 
        fp = Chem.rdmolops.LayeredFingerprint(mol)
    else : 
        print("fingerfrint selection error!")
        
    smiles_list.append(row['smiles'])   
    fps.append(fp)
    enc_y.append(target)
  except : 
    err_smiles.append(row['smiles'])
    pass

np_fps = []
for fp in fps:
  arr = numpy.zeros((1,))
  DataStructs.ConvertToNumpyArray(fp, arr)
  np_fps.append(arr)

np_fps_array = numpy.array(np_fps)

# print("변환 에러난 smiles 개수 : ", len(err_smiles), err_smiles)

x_train_res, y_train_res = np_fps_array, np.array(enc_y)
train = pd.DataFrame(data=x_train_res)
train['label'] = y_train_res

d = pd.DataFrame(columns = ['smiles','Type'] )
d['smiles'] = smiles_list
d['Type'] = enc_y

#모든 물질에 대한 fingerprint를 string형태로 바꾼다(비교하기위함).
mychems = []
for item in np_fps:
    #print(item)
    item = np.array(item,dtype=int) #왜 굳이 두번? int형으로 추가하려면 이렇게 하면 되는구나....
    s = item.tolist() #넘파이어레이를 리스트로 바꾼다. 
    t = [str(i) for i in s]
    mychems.append(''.join(t))

i = 0
counter = 0
chemdict = {} #딗셔너리.
listofdups = []
for item in mychems:
    try:
        chemdict[str(item)].append(i)
        #print('dup found')
        for j in range(len(chemdict[str(item)])):
            if (d['Type'][i] != d['Type'][chemdict[str(item)][j]]) :
                listofdups.append(i)
                counter+=1
    except: 
        #print('adding new')
        chemdict[str(item)] = []
        chemdict[str(item)].append(i)
    i+=1
# print(str(counter)+' '+str(len(list(set(listofdups)))))
#smote적용하기 전에서 listofdups를 빼면 된다!

dups_list = list(set(listofdups))

dups_list_0 = []
for index in dups_list : 
  if train.iloc[index].label == 0 :
    dups_list_0.append(index)

train = train.drop(dups_list_0)

#분산이 0인 feature 제거
train = train.loc[ :, train.std() > 0]



# rskf = RepeatedStratifiedKFold(n_splits=10, n_repeats=10, random_state=36851234) 
rskf = StratifiedKFold(n_splits = 10,shuffle =True, random_state = 42)
sme = SMOTEENN(random_state=42,sampling_strategy = "minority")

X = np.array( train.drop('label', axis =1) )
y = np.array(train.label)

count = 0 
rep = 0

metric_df = pd.DataFrame(columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy'])
metric_fold_df = pd.DataFrame(columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy'])

for train_index, test_index in rskf.split(X, y): 
  X_train, X_test = X[train_index], X[test_index]
  y_train, y_test = y[train_index], y[test_index]
  if ss in ['NVS_ADME_hCYP1A2' , 'NVS_ADME_hCYP2B6' , 'NCCT_TPO_AUR_dn'] : 
    pass
  else : 
    print("SMOTEENN fitiing....",ffpp, ss)
    X_train, y_train = sme.fit_sample(X_train, list(y_train) )
    print("....End fitiing",ffpp, ss)
  
  clf = RandomForestClassifier()
  clf.fit(X_train, y_train)

  result =  clf.predict_proba(X_test) # 첫 클래스의 예측확률, 두번째 클래스의 예측 확률 어떤것이 0, 1이지?
  y_pred = clf.predict(X_test)
  conf_mat = confusion_matrix(y_test,y_pred)
  tn, fp, fn, tp = conf_mat.ravel()

  precision_l, recall_l, thresholds = precision_recall_curve(y_test, result[:,1])
# Use AUC function to calculate the area under the curve of precision recall curve

  auc_pr = auc(recall_l, precision_l)
  auc_roc =  roc_auc_score(y_test,result[:,1] )
  recall = tp/(tp+fn) # 실제 1인 것 중 모델이 1이라 한것의 비율
  specificity = tn / (fp+tn) # 실제 0인 것중 모델이 0이라한것의 비율
  b_a = (recall + specificity) / 2
  precision =  tp / (tp+fp)
  F1 = 2* (precision * recall) / (precision + recall)
  MCC = matthews_corrcoef(y_test,y_pred)
  accuracy = clf.score(X_test,y_test)


  metric_fold_df = metric_fold_df.append(pd.DataFrame([[auc_roc,auc_pr,b_a,recall,precision,F1,MCC,accuracy]],columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy']) )
  count +=1
  # print(ffpp, ss, count)
  if count % 10 == 0 :
    average = metric_fold_df.mean()
    std = metric_fold_df.std()
    metric_fold_df = metric_fold_df.append(average.to_frame().T)
    metric_fold_df = metric_fold_df.append(std.to_frame().T)
    metric_fold_df = round(metric_fold_df ,4)
    metric_fold_df.index = [str(rep) +'_' +  str(i) for i in range(10)]+ [str(rep)+'_Mean' , str(rep)+'_SD']
    metric_df = metric_df.append(metric_fold_df)
    metric_fold_df = pd.DataFrame(columns = ['AUC','AUC_PR','B_A','Recall','Precision','F1','MCC','Accuracy'])
    rep += 1
    # print(ffpp, ss, rep)
  

#전체 평균내기.
bool_list = [] 
for i in metric_df.index :
  if'Mean' in i  or 'SD' in i : 
    bool_list.append(False) 
  else : 
    bool_list.append(True)

average = metric_df[bool_list].mean().to_frame().T
average.index = ['Mean']
std = metric_df[bool_list].std().to_frame().T
std.index =['SD']

metric_df = metric_df.append(round(average,4) )
metric_df = metric_df.append(round(std,4))
metric_df.to_csv(dir_path+"metric/"+ffpp+'/'+algorithm+'/'+ss+"_metric.csv")
print(ffpp, ss, 'end')
  

RDKit WARNING: [18:16:32] WARNING: not removing hydrogen atom without neighbors
[18:16:32] WARNING: not removing hydrogen atom without neighbors
RDKit WARNING: [18:16:32] WARNING: not removing hydrogen atom without neighbors
[18:16:32] WARNING: not removing hydrogen atom without neighbors
RDKit ERROR: [18:16:33] Explicit valence for atom # 0 F, 2, is greater than permitted
[18:16:33] Explicit valence for atom # 0 F, 2, is greater than permitted
RDKit ERROR: [18:16:33] Explicit valence for atom # 4 C, 5, is greater than permitted
[18:16:33] Explicit valence for atom # 4 C, 5, is greater than permitted
RDKit ERROR: [18:16:33] Explicit valence for atom # 0 O, 3, is greater than permitted
[18:16:33] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [18:16:33] Explicit valence for atom # 0 O, 3, is greater than permitted
[18:16:33] Explicit valence for atom # 0 O, 3, is greater than permitted
RDKit ERROR: [18:16:33] Explicit valence for atom # 2 Cl, 2, is greater th

SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist
SMOTEENN fitiing.... rdkit TOX21_ELG1_LUC_Agonist
....End fitiing rdkit TOX21_ELG1_LUC_Agonist


NameError: name 'algorithm' is not defined

In [ ]:
auc(recall_l, precision_l)

In [ ]:
auc(recall_l, precision_l)

In [ ]:
recall_l

In [ ]:
precision_l

In [ ]:
len(smiles_list)

In [15]:
metric_df

AUC  AUC_PR     B_A  Recall  Precision      F1     MCC  Accuracy
0_0     0.8227  0.0407  0.5000  0.0000        NaN     NaN  0.0000    0.9938
0_1     0.8125  0.3656  0.5988  0.2000     0.3333  0.2500  0.2547    0.9926
0_2     0.7839  0.3317  0.5994  0.2000     0.5000  0.2857  0.3137    0.9938
0_3     0.7301  0.0602  0.4994  0.0000     0.0000     NaN -0.0028    0.9926
0_4     0.8968  0.0843  0.4975  0.0000     0.0000     NaN -0.0055    0.9889
0_5     0.6764  0.2167  0.6000  0.2000     1.0000  0.3333  0.4461    0.9951
0_6     0.8844  0.0724  0.5994  0.2000     0.5000  0.2857  0.3137    0.9938
0_7     0.6393  0.2550  0.6238  0.2500     0.3333  0.2857  0.2856    0.9938
0_8     0.7652  0.2118  0.5944  0.2000     0.1000  0.1333  0.1339    0.9840
0_9     0.8473  0.0371  0.4994  0.0000     0.0000     NaN -0.0028    0.9926
0_Mean  0.7859  0.1675  0.5612  0.1250     0.3074  0.2623  0.1737    0.9921
0_SD    0.0849  0.1242  0.0540  0.1087     0.3320  0.0685  0.1695    0.0033
Mean    0.7859  0.1676  0.5612  0.1250     0.3074  0.2623  0.1737    0.9921
SD      0.0849  0.1242  0.0541  0.1087     0.3320  0.0685  0.1695    0.0033